### A cluster has been created for this demo
To run this demo, just select the cluster `dbdemos-llm-rag-chatbot-jason_bricks_std` from the dropdown menu ([open cluster configuration](https://dbc-458303b2-a0c9.cloud.databricks.com/#setting/clusters/0112-071913-b6023fae/configuration)). <br />
*Note: If the cluster was deleted after 30 days, you can re-create it with `dbdemos.create_cluster('llm-rag-chatbot')` or re-install the demo: `dbdemos.install('llm-rag-chatbot')`*


# 1/ Data preparation for LLM Chatbot RAG

## Building and indexing our knowledge base into Databricks Vector Search

<img src="https://github.com/databricks-demos/dbdemos-resources/blob/main/images/product/chatbot-rag/llm-rag-self-managed-flow-1.png?raw=true" style="float: right; width: 800px; margin-left: 10px">

In this notebook, we'll ingest our documentation pages and index them with a Vector Search index to help our chatbot provide better answers.

Preparing high quality data is key for your chatbot performance. We recommend taking time to implement these next steps with your own dataset.

Thankfully, Lakehouse AI provides state of the art solutions to accelerate your AI and LLM projects, and also simplifies data ingestion and preparation at scale.

For this example, we will use Databricks documentation from [docs.databricks.com](docs.databricks.com):
- Download the web pages
- Split the pages in small chunks of text
- Compute the embeddings using a Databricks Foundation model as part of our Delta Table
- Create a Vector Search index based on our Delta Table  

<!-- Collect usage data (view). Remove it to disable collection or disable tracker during installation. View README for more details.  -->
<img width="1px" src="https://ppxrzfxige.execute-api.us-west-2.amazonaws.com/v1/analytics?category=data-science&org_id=1126084104782633&notebook=%2F01-quickstart%2F01-Data-Preparation-and-Index&demo_name=llm-rag-chatbot&event=VIEW&path=%2F_dbdemos%2Fdata-science%2Fllm-rag-chatbot%2F01-quickstart%2F01-Data-Preparation-and-Index&version=1">

In [0]:
%pip install mlflow==2.9.0 lxml==4.9.3 transformers==4.30.2 langchain==0.0.344 databricks-vectorsearch==0.22
dbutils.library.restartPython()

Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.
  Using cached mlflow-2.9.0-py3-none-any.whl (19.1 MB)
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.9/7.9 MB 19.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.2/7.2 MB 55.5 MB/s eta 0:00:00
  Using cached langchain-0.0.344-py3-none-any.whl (1.9 MB)
  Using cached databricks_vectorsearch-0.22-py3-none-any.whl (8.5 kB)
  Using cached docker-6.1.3-py3-none-any.whl (148 kB)
  Using cached querystring_parser-1.2.4-py2.py3-none-any.whl (7.9 kB)
  Using cached alembic-1.13.1-py3-none-any.whl (233 kB)
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 60.7 MB/s eta 0:00:00
  Using cached langchain_core-0.0.13-py3-none-any.whl (188 kB)
  Using cached packaging-23.2-py3-none-any.whl (53 kB)
  Attempting uninstall: tokenizers
    Found existing installation: tokenizers 0.14.0
    Not uninstalling tokenizers at /databricks/python3/lib/python3.10/site-packages, outsid

In [0]:
%run ../_resources/00-init $reset_all_data=false

USE CATALOG `main`
using catalog.database `main`.`rag_chatbot`


DataFrame[]

## Extracting Databricks documentation sitemap and pages

<img src="https://github.com/databricks-demos/dbdemos-resources/blob/main/images/product/chatbot-rag/llm-rag-self-managed-prep-1.png?raw=true" style="float: right; width: 600px; margin-left: 10px">

First, let's create our raw dataset as a Delta Lake table.

For this demo, we will directly download a few documentation pages from `docs.databricks.com` and save the HTML content.

Here are the main steps:

- Run a quick script to extract the page URLs from the `sitemap.xml` file
- Download the web pages
- Use BeautifulSoup to extract the ArticleBody
- Save the HTML results in a Delta Lake table

In [0]:
if not spark.catalog.tableExists("raw_documentation") or spark.table("raw_documentation").isEmpty():
    # Download Databricks documentation to a DataFrame (see _resources/00-init for more details)
    doc_articles = download_databricks_documentation_articles()
    #Save them as a raw_documentation table
    doc_articles.write.mode('overwrite').saveAsTable("raw_documentation")

display(spark.table("raw_documentation").limit(2))

url text https://docs.databricks.com/en/delta/update-schema.html 
 
 Update Delta Lake table schema 
 Delta Lake lets you update the schema of a table. The following types of changes are supported: 
 
 Adding new columns (at arbitrary positions) 
 Reordering existing columns 
 Renaming existing columns 
 
 You can make these changes explicitly using DDL or implicitly using DML. 
 
 Important 
 When you update a Delta table schema, streams that read from that table terminate. If you want the stream to continue you must restart it. 
 For recommended methods, see Production considerations for Structured Streaming . 
 
 
 Explicitly update schema to add columns 
 ALTER TABLE table_name ADD COLUMNS ( col_name data_type [ COMMENT col_comment ] [ FIRST | AFTER colA_name ], ...) 
 
 
 By default, nullability is true . 
 To add a column to a nested field, use: 
 ALTER TABLE table_name ADD COLUMNS ( col_name . nested_col_name data_type [ COMMENT col_comment ] [ FIRST | AFTER colA_name ], ...) 
 
 
 For example, if the schema before running ALTER TABLE boxes ADD COLUMNS (colB.nested STRING AFTER field1) is: 
 - root 
 | - colA 
 | - colB 
 | +- field1 
 | +- field2 
 
 
 the schema after is: 
 - root 
 | - colA 
 | - colB 
 | +- field1 
 | +- nested 
 | +- field2 
 
 
 
 Note 
 Adding nested columns is supported only for structs. Arrays and maps are not supported. 
 
 
 
 Explicitly update schema to change column comment or ordering 
 ALTER TABLE table_name ALTER [ COLUMN ] col_name ( COMMENT col_comment | FIRST | AFTER colA_name ) 
 
 
 To change a column in a nested field, use: 
 ALTER TABLE table_name ALTER [ COLUMN ] col_name . nested_col_name ( COMMENT col_comment | FIRST | AFTER colA_name ) 
 
 
 For example, if the schema before running ALTER TABLE boxes ALTER COLUMN colB.field2 FIRST is: 
 - root 
 | - colA 
 | - colB 
 | +- field1 
 | +- field2 
 
 
 the schema after is: 
 - root 
 | - colA 
 | - colB 
 | +- field2 
 | +- field1 
 
 
 
 
 Explicitly update schema to replace columns 
 ALTER TABLE table_name REPLACE COLUMNS ( col_name1 col_type1 [ COMMENT col_comment1 ], ...) 
 
 
 For example, when running the following DDL: 
 ALTER TABLE boxes REPLACE COLUMNS ( colC STRING , colB STRUCT < field2 : STRING , nested : STRING , field1 : STRING > , colA STRING ) 
 
 
 if the schema before is: 
 - root 
 | - colA 
 | - colB 
 | +- field1 
 | +- field2 
 
 
 the schema after is: 
 - root 
 | - colC 
 | - colB 
 | +- field2 
 | +- nested 
 | +- field1 
 | - colA 
 
 
 
 
 Explicitly update schema to rename columns 
 
 Preview 
 This feature is in Public Preview . 
 
 
 Note 
 This feature is available in Databricks Runtime 10.2 and above. 
 
 To rename columns without rewriting any of the columns’ existing data, you must enable column mapping for the table. See Rename and drop columns with Delta Lake column mapping . 
 To rename a column: 
 ALTER TABLE table_name RENAME COLUMN old_col_name TO new_col_name 
 
 
 To rename a nested field: 
 ALTER TABLE table_name RENAME COLUMN col_name . old_nested_field TO new_nested_field 
 
 
 For example, when you run the following command: 
 ALTER TABLE boxes RENAME COLUMN colB . field1 TO field001 
 
 
 If the schema before is: 
 - root 
 | - colA 
 | - colB 
 | +- field1 
 | +- field2 
 
 
 Then the schema after is: 
 - root 
 | - colA 
 | - colB 
 | +- field001 
 | +- field2 
 
 
 See Rename and drop columns with Delta Lake column mapping . 
 
 
 Explicitly update schema to drop columns 
 
 Preview 
 This feature is in Public Preview . 
 
 
 Note 
 This feature is available in Databricks Runtime 11.0 and above. 
 
 To drop columns as a metadata-only operation without rewriting any data files, you must enable column mapping for the table. See Rename and drop columns with Delta Lake column mapping . 
 
 Important 
 Dropping a column from metadata does not delete the underlying data for the column in files. To purge the dropped column data, you can use REORG TABLE to rewrite files. You can then use V


### Splitting documentation pages into small chunks

<img src="https://github.com/databricks-demos/dbdemos-resources/blob/main/images/product/chatbot-rag/llm-rag-self-managed-prep-2.png?raw=true" style="float: right; width: 600px; margin-left: 10px">

LLM models typically have a maximum input context length, and you won't be able to compute embeddings for very long texts.
In addition, the longer your context length is, the longer it will take for the model to provide a response.

Document preparation is key for your model to perform well, and multiple strategies exist depending on your dataset:

- Split document into small chunks (paragraph, h2...)
- Truncate documents to a fixed length
- The chunk size depends on your content and how you'll be using it to craft your prompt. Adding multiple small doc chunks in your prompt might give different results than sending only a big one
- Split into big chunks and ask a model to summarize each chunk as a one-off job, for faster live inference
- Create multiple agents to evaluate each bigger document in parallel, and ask a final agent to craft your answer...


### Splitting our big documentation pages in smaller chunks (h2 sections)

<img src="https://github.com/databricks-demos/dbdemos-resources/blob/main/images/product/chatbot-rag/chunk-window-size.png?raw=true" style="float: right" width="700px">
<br/>
In this demo, we have big documentation articles, which are too long for the prompt to our model. 

We won't be able to use multiple documents as RAG context as they would exceed our max input size. Some recent studies also suggest that bigger window size isn't always better, as the LLMs seem to focus on the beginning and end of your prompt.

In our case, we'll split these articles between HTML `h2` tags, remove HTML and ensure that each chunk is less than 500 tokens using LangChain. 

#### LLM Window size and Tokenizer

The same sentence might return different tokens for different models. LLMs are shipped with a `Tokenizer` that you can use to count tokens for a given sentence (usually more than the number of words) (see [Hugging Face documentation](https://huggingface.co/docs/transformers/main/tokenizer_summary) or [OpenAI](https://github.com/openai/tiktoken))

Make sure the tokenizer you'll be using here matches your model. We'll be using the `transformers` library to count llama2 tokens with its tokenizer. This will also keep our document token size below our embedding max size (1024).

<br/>
<br style="clear: both">
<div style="background-color: #def2ff; padding: 15px;  border-radius: 30px; ">
  <strong>Information</strong><br/>
  Remember that the following steps are specific to your dataset. This is a critical part to building a successful RAG assistant.
  <br/> Always take time to manually review the chunks created and ensure that they make sense and contain relevant information.
</div>

In [0]:
from langchain.text_splitter import HTMLHeaderTextSplitter, RecursiveCharacterTextSplitter
from transformers import AutoTokenizer

max_chunk_size = 500

tokenizer = AutoTokenizer.from_pretrained("hf-internal-testing/llama-tokenizer")
text_splitter = RecursiveCharacterTextSplitter.from_huggingface_tokenizer(tokenizer, chunk_size=max_chunk_size, chunk_overlap=50)
html_splitter = HTMLHeaderTextSplitter(headers_to_split_on=[("h2", "header2")])

# Split on H2, but merge small h2 chunks together to avoid too small. 
def split_html_on_h2(html, min_chunk_size = 20, max_chunk_size=500):
  if not html:
      return []
  h2_chunks = html_splitter.split_text(html)
  chunks = []
  previous_chunk = ""
  # Merge chunks together to add text before h2 and avoid too small docs.
  for c in h2_chunks:
    # Concat the h2 (note: we could remove the previous chunk to avoid duplicate h2)
    content = c.metadata.get('header2', "") + "\n" + c.page_content
    if len(tokenizer.encode(previous_chunk + content)) <= max_chunk_size/2:
        previous_chunk += content + "\n"
    else:
        chunks.extend(text_splitter.split_text(previous_chunk.strip()))
        previous_chunk = content + "\n"
  if previous_chunk:
      chunks.extend(text_splitter.split_text(previous_chunk.strip()))
  # Discard too small chunks
  return [c for c in chunks if len(tokenizer.encode(c)) > min_chunk_size]

# Let's create a user-defined function (UDF) to chunk all our documents with spark
@pandas_udf("array<string>")
def parse_and_split(docs: pd.Series) -> pd.Series:
    return docs.apply(split_html_on_h2)
  
# Let's try our chunking function
html = spark.table("raw_documentation").limit(1).collect()[0]['text']
split_html_on_h2(html)

2024-01-20 19:38:58.927073: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.


['Update Delta Lake table schema  \nDelta Lake lets you update the schema of a table. The following types of changes are supported:  \nAdding new columns (at arbitrary positions)  \nReordering existing columns  \nRenaming existing columns  \nYou can make these changes explicitly using DDL or implicitly using DML.  \nImportant  \nWhen you update a Delta table schema, streams that read from that table terminate. If you want the stream to continue you must restart it.  \nFor recommended methods, see Production considerations for Structured Streaming.  \nExplicitly update schema to add columns',
 'Explicitly update schema to add columns\nALTER TABLE table_name ADD COLUMNS (col_name data_type [COMMENT col_comment] [FIRST|AFTER colA_name], ...)  \nBy default, nullability is true.  \nTo add a column to a nested field, use:  \nALTER TABLE table_name ADD COLUMNS (col_name.nested_col_name data_type [COMMENT col_comment] [FIRST|AFTER colA_name], ...)  \nFor example, if the schema before running A

## What's required for our Vector Search Index

<img src="https://github.com/databricks-demos/dbdemos-resources/blob/main/images/product/chatbot-rag/databricks-vector-search-type.png?raw=true" style="float: right" width="800px">

Databricks provides multiple types of vector search indexes:

- **Managed embeddings**: you provide a text column and endpoint name and Databricks synchronizes the index with your Delta table 
- **Self Managed embeddings**: you compute the embeddings and save them as a field of your Delta Table, Databricks will then synchronize the index
- **Direct index**: when you want to use and update the index without having a Delta Table

In this demo, we will show you how to setup a **Self-managed Embeddings** index. 

To do so, we will have to first compute the embeddings of our chunks and save them as a Delta Lake table field as `array&ltfloat&gt`

## Introducing Databricks BGE Embeddings Foundation Model endpoints

<img src="https://github.com/databricks-demos/dbdemos-resources/blob/main/images/product/chatbot-rag/llm-rag-self-managed-prep-4.png?raw=true" style="float: right; width: 600px; margin-left: 10px">

Foundation Models are provided by Databricks, and can be used out-of-the-box.

Databricks supports several endpoint types to compute embeddings or evaluate a model:
- A **foundation model endpoint**, provided by Databricks (ex: llama2-70B, MPT...)
- An **external endpoint**, acting as a gateway to an external model (ex: Azure OpenAI)
- A **custom**, fined-tuned model hosted on Databricks model service

Open the [Model Serving Endpoint page](/ml/endpoints) to explore and try the foundation models.

For this demo, we will use the foundation model `BGE` (embeddings) and `llama2-70B` (chat). <br/><br/>

<img src="https://github.com/databricks-demos/dbdemos-resources/blob/main/images/product/chatbot-rag/databricks-foundation-models.png?raw=true" width="600px" >

In [0]:
import mlflow.deployments
deploy_client = mlflow.deployments.get_deploy_client("databricks")

response = deploy_client.predict(endpoint="databricks-bge-large-en", inputs={"input": ["What is Apache Spark?"]})
embeddings = [e['embedding'] for e in response.data]
print(embeddings)

[[0.0186004638671875, -0.0141448974609375, -0.0574951171875, 0.0034027099609375, 0.008453369140625, -0.0216064453125, -0.02471923828125, -0.004688262939453125, 0.0136566162109375, 0.050384521484375, -0.0272064208984375, -0.01470184326171875, 0.054718017578125, -0.0538330078125, -0.01035308837890625, -0.0162200927734375, -0.0188140869140625, -0.017242431640625, -0.051300048828125, 0.0177764892578125, 0.00434112548828125, 0.0284423828125, -0.055633544921875, -0.037689208984375, -0.001373291015625, 0.0203704833984375, -0.046661376953125, 0.01580810546875, 0.0938720703125, 0.0195770263671875, -0.044647216796875, -0.0124359130859375, -0.0062255859375, -0.0293121337890625, 0.04327392578125, -0.02557373046875, 0.049468994140625, 0.03228759765625, -0.06011962890625, -0.0126495361328125, 0.0218658447265625, -0.0099945068359375, 0.0135650634765625, -0.04058837890625, -0.0777587890625, -0.040863037109375, 0.003063201904296875, -0.03369140625, -0.01284027099609375, -0.040985107421875, -0.039794921

In [0]:
%sql
--Note that we need to enable Change Data Feed on the table to create the index
CREATE TABLE IF NOT EXISTS databricks_documentation (
  id BIGINT GENERATED BY DEFAULT AS IDENTITY,
  url STRING,
  content STRING,
  embedding ARRAY <FLOAT>
) TBLPROPERTIES (delta.enableChangeDataFeed = true); 

### Computing the chunk embeddings and saving them to our Delta Table

The last step is to compute an embedding for all our documentation chunks. Let's create a udf to compute the embeddings using the foundation model endpoint.

*Note that this part would typically be setup as a production-grade job, running as soon as a new documentation page is updated. <br/> This could be setup as a Delta Live Table pipeline to incrementally consume updates.*

In [0]:
import mlflow.deployments
deploy_client = mlflow.deployments.get_deploy_client("databricks")

@pandas_udf("array<float>")
def get_embedding(contents: pd.Series) -> pd.Series:
    def get_embeddings(batch):
        #Note: this will gracefully fail if an exception is thrown during embedding creation (add try/except if needed) 
        response = deploy_client.predict(endpoint="databricks-bge-large-en", inputs={"input": batch})
        return [e['embedding'] for e in response.data]

    # Splitting the contents into batches of 150 items each, since the embedding model takes at most 150 inputs per request.
    max_batch_size = 150
    batches = [contents.iloc[i:i + max_batch_size] for i in range(0, len(contents), max_batch_size)]

    # Process each batch and collect the results
    all_embeddings = []
    for batch in batches:
        all_embeddings += get_embeddings(batch.tolist())

    return pd.Series(all_embeddings)

In [0]:
(spark.table("raw_documentation")
      .filter('text is not null')
      .withColumn('content', F.explode(parse_and_split('text')))
      .withColumn('embedding', get_embedding('content'))
      .drop("text")
      .write.mode('overwrite').saveAsTable("databricks_documentation"))

display(spark.table("databricks_documentation"))

id url content embedding 2580 https://docs.databricks.com/en/dev-tools/cli/install.html Install or update the Databricks CLI 
Note 
This information applies to Databricks CLI versions 0.205 and above, which are in Public Preview. To find your version of the Databricks CLI, run databricks -v. 
This article describes how to install or update the Databricks CLI. See What is the Databricks CLI?. 
Install
Install
To install Databricks CLI version 0.205 or above: 
Linux or macOS: Use Homebrew, curl, or source builds. 
Windows: Use Windows Subsystem for Linux (WSL) or source builds.

Update
Update
To update an earlier installation of Databricks CLI version 0.205 or above: 
Linux or macOS: Use Homebrew, curl, or source builds. 
Windows: Use Windows Subsystem for Linux (WSL) or source builds.

Homebrew installation for Linux or macOS List(-0.013252258, -0.009567261, -0.01600647, 0.006713867, -0.010238647, -0.021194458, 0.015960693, 0.0072631836, 0.017059326, 0.03643799, 0.00242424, 0.014091492, 0.0046577454, -0.05432129, 0.013000488, 0.020477295, -0.026885986, 0.02734375, -0.017623901, 0.014335632, 0.05014038, 0.028762817, -0.06854248, 0.0010137558, -0.0206604, 0.041137695, -0.008300781, 0.01512146, 0.059936523, 0.04147339, -0.03842163, -0.0063438416, 0.002494812, -0.05001831, -0.0023269653, 0.009315491, 0.0026512146, 0.0038852692, -0.02835083, -0.01966858, -0.0035190582, 0.024307251, 0.04034424, -0.023544312, -0.053344727, -0.04385376, -0.036712646, -0.024627686, -0.0063934326, 0.0046424866, -0.033996582, -0.0026416779, 0.076171875, -0.030975342, 0.013214111, -0.015449524, -0.025497437, 0.028030396, -0.057678223, 0.014091492, -0.0016899109, 0.036956787, 0.011741638, -0.023361206, 0.06951904, 0.022506714, 0.004688263, -0.016494751, -0.0027713776, -0.02116394, -0.060638428, 0.08947754, -0.013793945, -0.058166504, -0.015266418, 0.0046424866, 0.046813965, 0.027511597, -0.043060303, 0.040374756, 0.030044556, 0.0058670044, 0.016296387, 0.021560669, -0.0066719055, -0.01965332, 0.048339844, -0.0077934265, -0.008239746, 0.031433105, -5.9890747E-4, 0.026107788, 0.004962921, 0.024765015, 0.046417236, 0.005290985, -0.029556274, -0.011116028, 0.008529663, -0.0031089783, 0.003921509, 0.024276733, 0.018188477, 0.026855469, 0.0317688, -0.0033130646, 0.02444458, 0.0053215027, -0.0115356445, -0.02357483, 0.024536133, -0.0062217712, 0.00340271, -0.015457153, 0.012466431, -0.033111572, 0.042541504, 0.055145264, -0.06866455, -0.03753662, 0.064208984, 0.010795593, 0.013168335, -0.053253174, -0.04031372, -0.026519775, -0.035827637, 0.028121948, -0.0076560974, -0.059753418, -0.007987976, -0.0141067505, 0.030181885, 0.030517578, -0.029525757, 0.0014190674, 0.014678955, 0.005405426, 0.033935547, -0.029144287, 0.021438599, -0.048858643, -0.016357422, 0.082458496, 0.022506714, 0.007396698, -0.008735657, -0.035858154, -0.048095703, 0.044952393, -0.03616333, 0.025650024, 0.052459717, -0.009475708, 0.0063705444, 0.014656067, -0.032196045, 0.039764404, 0.023605347, 0.026550293, -0.030731201, 0.012168884, -0.032348633, 0.021911621, 0.012649536, 0.043273926, -0.011940002, 0.018692017, 0.011726379, -0.016830444, -0.003353119, -0.028015137, 0.0014591217, 0.010528564, 0.037597656, 0.031799316, 0.0069122314, 0.024230957, 0.012062073, 0.031341553, -0.025436401, 0.017608643, 0.028427124, -0.010658264, 7.958412E-4, 0.017074585, -0.0018453598, -0.031311035, -0.016464233, 0.008720398, -0.030319214, 0.072021484, 0.007106781, 0.016067505, -0.045532227, -5.903244E-4, -0.05734253, 0.056365967, 0.025726318, -0.035736084, -0.033233643, 0.02166748, 0.009239197, 0.0012636185, 0.040802002, -0.061828613, 0.008453369, -0.0017871857, 0.025039673, -0.028869629, 0.051696777, -0.0104522705, -0.007381439, -0.001364708, 0.072265625, -0.007972717, -0.015960693, -0.0024108887, -0.027618408, -0.039764404, 0.025619507, 0.011978149, 0.0423584, 0.04925537, -0.022583008, -0.01197052, -0.0104522705, 0.009384155, -0.051574707, 0.026519775, 0.0014591217, 0.056762695, 0.026916504, 0.009307861, -0.0255279


### Our dataset is now ready! Let's create our Self-Managed Vector Search Index.

<img src="https://github.com/databricks-demos/dbdemos-resources/blob/main/images/product/chatbot-rag/llm-rag-self-managed-prep-3.png?raw=true" style="float: right; width: 600px; margin-left: 10px">

Our dataset is now ready. We chunked the documentation page into small sections, computed the embeddings and saved it as a Delta Lake table.

Next, we'll configure Databricks Vector Search to ingest data from this table.

Vector search index uses a Vector search endpoint to serve the embeddings (you can think about it as your Vector Search API endpoint). <br/>
Multiple Indexes can use the same endpoint. Let's start by creating one.

In [0]:
from databricks.vector_search.client import VectorSearchClient
vsc = VectorSearchClient()

if VECTOR_SEARCH_ENDPOINT_NAME not in [e['name'] for e in vsc.list_endpoints().get('endpoints', [])]:
    vsc.create_endpoint(name=VECTOR_SEARCH_ENDPOINT_NAME, endpoint_type="STANDARD")

wait_for_vs_endpoint_to_be_ready(vsc, VECTOR_SEARCH_ENDPOINT_NAME)
print(f"Endpoint named {VECTOR_SEARCH_ENDPOINT_NAME} is ready.")

[NOTICE] Using a notebook authentication token. Recommended for development only. For improved performance, please use Service Principal based authentication. To disable this message, pass disable_notice=True to VectorSearchClient().
Endpoint named dbdemos_vs_endpoint is ready.



You can view your endpoint on the [Vector Search Endpoints UI](#/setting/clusters/vector-search). Click on the endpoint name to see all indexes that are served by the endpoint.

In [0]:
from databricks.sdk import WorkspaceClient
import databricks.sdk.service.catalog as c

#The table we'd like to index
source_table_fullname = f"{catalog}.{db}.databricks_documentation"
# Where we want to store our index
vs_index_fullname = f"{catalog}.{db}.databricks_documentation_vs_index"

if not index_exists(vsc, VECTOR_SEARCH_ENDPOINT_NAME, vs_index_fullname):
  print(f"Creating index {vs_index_fullname} on endpoint {VECTOR_SEARCH_ENDPOINT_NAME}...")
  vsc.create_delta_sync_index(
    endpoint_name=VECTOR_SEARCH_ENDPOINT_NAME,
    index_name=vs_index_fullname,
    source_table_name=source_table_fullname,
    pipeline_type="TRIGGERED",
    primary_key="id",
    embedding_dimension=1024, #Match your model embedding size (bge)
    embedding_vector_column="embedding"
  )
else:
  #Trigger a sync to update our vs content with the new data saved in the table
  vsc.get_index(VECTOR_SEARCH_ENDPOINT_NAME, vs_index_fullname).sync()

#Let's wait for the index to be ready and all our embeddings to be created and indexed
wait_for_index_to_be_ready(vsc, VECTOR_SEARCH_ENDPOINT_NAME, vs_index_fullname)
print(f"index {vs_index_fullname} on table {source_table_fullname} is ready")

Creating index main.rag_chatbot.databricks_documentation_vs_index on endpoint dbdemos_vs_endpoint...
Error processing request 400 Client Error: Bad Request for url: https://oregon.cloud.databricks.com/api/2.0/vector-search/endpoints/dbdemos_vs_endpoint/indexes


---------------------------------------------------------------------------
HTTPError                                 Traceback (most recent call last)
File /local_disk0/.ephemeral_nfs/envs/pythonEnv-120cbf1c-a34b-4f54-a649-07a949bbfb1e/lib/python3.10/site-packages/databricks/vector_search/utils.py:123, in RequestUtils.issue_request(url, token, method, params, json, verify)
    122 try:
--> 123     response.raise_for_status()
    124 except Exception as e:

File /databricks/python/lib/python3.10/site-packages/requests/models.py:1021, in Response.raise_for_status(self)
   1020 if http_error_msg:
-> 1021     raise HTTPError(http_error_msg, response=self)

HTTPError: 400 Client Error: Bad Request for url: https://oregon.cloud.databricks.com/api/2.0/vector-search/endpoints/dbdemos_vs_endpoint/indexes

During handling of the above exception, another exception occurred:

Exception                                 Traceback (most recent call last)
File <command-4419281565496384>, line 11
     

## Searching for similar content

That's all we have to do. Databricks will automatically capture and synchronize new entries in your Delta Live Table.

Note that depending on your dataset size and model size, index creation can take a few seconds to start and index your embeddings.

Let's give it a try and search for similar content.

*Note: `similarity_search` also support a filters parameter. This is useful to add a security layer to your RAG system: you can filter out some sensitive content based on who is doing the call (for example filter on a specific department based on the user preference).*

In [0]:
import mlflow.deployments
deploy_client = mlflow.deployments.get_deploy_client("databricks")

question = "How can I track billing usage on my workspaces?"
response = deploy_client.predict(endpoint="databricks-bge-large-en", inputs={"input": [question]})
embeddings = [e['embedding'] for e in response.data]

results = vsc.get_index(VECTOR_SEARCH_ENDPOINT_NAME, vs_index_fullname).similarity_search(
  query_vector=embeddings[0],
  columns=["url", "content"],
  num_results=1)
docs = results.get('result', {}).get('data_array', [])
docs

[['https://docs.databricks.com/en/administration-guide/account-settings/usage.html',
  'Usage details\nUsage details\nIn the Usage details panel, you can view a list of detailed usage in DBU or the estimated cost in $USD in a table format. This panel’s data is always aggregated by workspace. The cost is also broken down into SKU groups. To view usage as totals (aggregated) or by SKU, use the graph in the settings panel instead.  \nTo toggle between estimated cost and DBUs, use the $USD/DBU picker.  \nUse the date range picker to specify an exact time range or choose among pre-defined options such as Last 6 months. The time ranges are in UTC time.  \nIf you have many workspaces, type the workspace name into the search field to filter results.  \nThe actual cost varies depending on your contract. You can adjust the cost-per-DBU for each SKU in the settings panel to change the cost estimate.\n\nPricing',
  0.6074996]]

## Next step: Deploy our chatbot model with RAG

We've seen how Databricks Lakehouse AI makes it easy to ingest and prepare your documents, and deploy a Vector Search index on top of it with just a few lines of code and configuration.

This simplifies and accelerates your data projects so that you can focus on the next step: creating your real-time chatbot endpoint with well-crafted prompt augmentation.

Open the [02-Deploy-RAG-Chatbot-Model]($./02-Deploy-RAG-Chatbot-Model) notebook to create and deploy a chatbot endpoint.